# Mimic of the DES night summary, but for Rubin Observatory

In [1]:
# This cell is only for setting parameter defaults
day_obs = "2027-11-10"
visit_db_fname = None

In [2]:
import datetime
import sys
import pandas as pd
import bokeh
import bokeh.io
import bokeh.plotting
import bokeh.models
import bokeh.transform
import bokeh.layouts
import sqlite3
import numpy as np
import healpy
import astropy
import colorcet
import healpy as hp
from astropy.visualization import ZScaleInterval
from astropy.time import Time
from lsst.resources import ResourcePath

In [3]:
import rubin_scheduler
import rubin_scheduler.utils
import rubin_scheduler.site_models
import schedview.compute.astro
import schedview.compute.visits
import uranography
import schedview.plot.visitmap

from rubin_sim import maf
from rubin_sim.data import get_baseline
from schedview.compute.camera import LsstCameraFootprintPerimeter
from rubin_scheduler.scheduler.model_observatory import ModelObservatory
from uranography.api import Planisphere, make_zscale_linear_cmap

In [4]:
bokeh.io.output_notebook()

Loading BokehJS ...

In [5]:
astropy.utils.iers.conf.iers_degraded_accuracy = 'ignore'

In [6]:
if visit_db_fname is None:
    visit_db_fname = get_baseline()

In [7]:
baseline_opsim_rp = ResourcePath(visit_db_fname)

In [8]:
day_obs_mjd = int(Time(day_obs).mjd)
day_obs_datetime = Time(day_obs_mjd, format='mjd').datetime
day_obs_date = datetime.date(day_obs_datetime.year, day_obs_datetime.month, day_obs_datetime.day)

In [9]:
band_cmap = bokeh.transform.factor_cmap(
    'filter',
    ('#56b4e9', '#008060', '#ff4000', '#850000', '#6600cc', '#000000'),
    ['u', 'g', 'r', 'i', 'z', 'y'])

In [10]:
fiducial_depth = {
                "u": 23.71,
                "g": 24.67,
                "r": 24.24,
                "i": 23.82,
                "z": 23.21,
                "y": 22.40,
}

In [11]:
observatory = ModelObservatory(init_load_length=1)
timezone = "Chile/Continental"

In [12]:
def visit_query(visit_resource_path, constraint):
    visits = schedview.collect.read_opsim(visit_db_fname, constraint=constraint)
    visits = schedview.compute.visits.add_day_obs(visits)
    visits = schedview.compute.visits.add_coords_tuple(visits)
    visits = schedview.compute.visits.add_maf_metric(
        visits, maf.TeffMetric(), 'teff', visit_db_fname, constraint, 'fiveSigmaDepth')
    visits = schedview.compute.visits.add_overhead(visits)
    
    return visits

In [13]:
visits = visit_query(
    baseline_opsim_rp,
    f"FLOOR(observationStartMJD-0.5)={day_obs_mjd}"
)

/sdf/group/rubin/user/neilsen/mambaforge/envs/ehn311/lib/python3.11/site-packages/erfa/core.py:154: ErfaWarning: ERFA function "dtf2d" yielded 1 of "dubious year (Note 6)"
  warnings.warn('ERFA function "{}" yielded {}'.format(func_name, wmsg),


Using fiducial depths for t_eff calculation from https://github.com/lsst-sims/smtn-002/blob/main/notebooks/teff_fiducial.ipynb commit e367d65.
These probably should be updated.

In [14]:
visits.head()

fieldRA  day_obs_mjd day_obs_date day_obs_iso8601  \
observationId                                                         
574815         273.872670        61719   2027-11-10      2027-11-10   
574816         270.391667        61719   2027-11-10      2027-11-10   
574817         268.038960        61719   2027-11-10      2027-11-10   
574818         264.623586        61719   2027-11-10      2027-11-10   
574819         265.785372        61719   2027-11-10      2027-11-10   

                fieldDec                                    coords  \
observationId                                                        
574815        -26.811630    (273.8726704470863, -26.8116301378763)   
574816        -27.213913  (270.39166680762236, -27.21391346970812)   
574817        -24.908881  (268.0389602290315, -24.908880893637512)   
574818        -25.149016    (264.623585662104, -25.14901606049597)   
574819        -22.539402  (265.78537200464865, -22.53940169452576)   

               observationStartMJD  flush_by_mjd  visitExposureTime filter  \
observationId                                                                
574815                61720.007980  61720.030973               15.0      i   
574816                61720.008220  61720.030973               15.0      i   
574817                61720.008461  61720.030973               15.0      i   
574818                61720.008702  61720.030973               15.0      i   
574819                61720.008937  61720.030973               15.0      i   

               ...     sunDec    moonRA   moonDec  moonDistance  solarElong  \
observationId  ...                                                            
574815         ... -17.184499  7.581837  8.625128     97.165109   45.585422   
574816         ... -17.184566  7.583519  8.626532    100.292213   42.508255   
574817         ... -17.184633  7.585203  8.627937    102.233614   40.266136   
574818         ... -17.184701  7.586883  8.629339    105.338848   37.191895   
574819         ... -17.184767  7.588527  8.630711    104.141007   38.137282   

               moonPhase   cummTelAz  scripted_id  \
observationId                                       
574815         78.955355 -104.870678            0   
574816         78.956333 -106.588953            0   
574817         78.957312 -105.108034            0   
574818         78.958290 -106.707225            0   
574819         78.959245 -103.664804            0   

                                       start_date  HA_hours  
observationId                                                
574815        2027-11-11 00:11:29.469806848+00:00  4.544933  
574816        2027-11-11 00:11:50.241490688+00:00  4.782785  
574817        2027-11-11 00:12:11.040894976+00:00  4.945426  
574818        2027-11-11 00:12:31.809601536+00:00  5.178903  
574819        2027-11-11 00:12:52.128139520+00:00  5.107110  

[5 rows x 53 columns]

In [15]:
visits.head()['start_date']

observationId
574815   2027-11-11 00:11:29.469806848+00:00
574816   2027-11-11 00:11:50.241490688+00:00
574817   2027-11-11 00:12:11.040894976+00:00
574818   2027-11-11 00:12:31.809601536+00:00
574819   2027-11-11 00:12:52.128139520+00:00
Name: start_date, dtype: datetime64[ns, UTC]

### Sun and Moon

In [16]:
day_obs_mjd = int(Time(day_obs).mjd)
day_obs_datetime = Time(day_obs_mjd, format='mjd').datetime
day_obs_date = datetime.date(day_obs_datetime.year, day_obs_datetime.month, day_obs_datetime.day)
night_events = schedview.compute.astro.night_events(day_obs_date)
night_events

MJD         LST                              UTC  \
event                                                                        
sunset           61719.964397  326.317054 2027-11-10 23:08:43.921000+00:00   
sun_n12_setting  61720.006751  341.606016 2027-11-11 00:09:43.253000+00:00   
sun_n18_setting  61720.029259  349.731393 2027-11-11 00:42:08.019000+00:00   
sun_n18_rising   61720.341286  102.368629 2027-11-11 08:11:27.145000+00:00   
sun_n12_rising   61720.363801  110.495932 2027-11-11 08:43:52.372000+00:00   
sunrise          61720.406151  125.783733 2027-11-11 09:44:51.427000+00:00   
moonrise         61720.879471  296.645446 2027-11-11 21:06:26.274000+00:00   
moonset          61720.318827   94.261095 2027-11-11 07:39:06.650000+00:00   
night_middle     61720.185274   46.050393 2027-11-11 04:26:47.674000+00:00   

                               Chile/Continental  
event                                             
sunset          2027-11-10 20:08:43.921000-03:00  
sun_n12_setting 2027-11-10 21:09:43.253000-03:00  
sun_n18_setting 2027-11-10 21:42:08.019000-03:00  
sun_n18_rising  2027-11-11 05:11:27.145000-03:00  
sun_n12_rising  2027-11-11 05:43:52.372000-03:00  
sunrise         2027-11-11 06:44:51.427000-03:00  
moonrise        2027-11-11 18:06:26.274000-03:00  
moonset         2027-11-11 04:39:06.650000-03:00  
night_middle    2027-11-11 01:26:47.674000-03:00

In [17]:
print(f"Moon phase: {visits['moonPhase'].median()}")

Moon phase: 79.63021777734996


## Conditions and statistics

### Numbers of exposures, and gaps between them

In [18]:
relative_start_time = (visits['observationStartMJD'].min() - night_events.loc['sun_n12_setting','MJD'])*60*24
print(f"Open shutter of first exposure: {relative_start_time} minutes before 12 degree evening twilight")

relative_end_time = ((visits['observationStartMJD'] + visits['visitTime']/(24*60*60)).max() - night_events.loc['sun_n12_rising','MJD'])*60*24
print(f"Close shutter time of last exposure: {-1*relative_end_time} minutes after 12 degree morning twilight")

total_time = ((visits['observationStartMJD'] + visits['visitTime']/(24*60*60)).max() - visits['observationStartMJD'].min())*24
print(f"Total wall clock time: {total_time} hours")

num_exposures = len(visits)
print(f"Number of exposures: {num_exposures}")

total_exptime = visits.visitExposureTime.sum()/(60*60)
print(f"Total open shutter time: {total_exptime} hours")

mean_gap_time = 60*60*(total_time - total_exptime)/(num_exposures - 1)
print(f"Mean gap time: {mean_gap_time} seconds")

median_gap_time = visits.overhead.median()
print(f"Median gap time: {median_gap_time} seconds")

Open shutter of first exposure: 1.7702803609427065 minutes before 12 degree evening twilight
Close shutter time of last exposure: 0.4208632686641067 minutes after 12 degree morning twilight
Total wall clock time: 8.532680777250789 hours
Number of exposures: 773
Total open shutter time: 6.05 hours
Mean gap time: 11.577267873190209 seconds
Median gap time: 8.800299062859267 seconds


## Histogram of gaps between exposures

In [19]:
bins = np.arange(0, 30)
hist, edges = np.histogram(visits.overhead, density=False, bins=bins)
p1 = bokeh.plotting.figure(title='Overhead', y_axis_label='Overhead (seconds)')
p1.quad(top=hist, bottom=0, left=edges[:-1], right=edges[1:],
         fill_color="skyblue", line_color="white")

p2 = bokeh.plotting.figure(title='Overhead vs. slew distance', y_axis_label='overhead (sec.)', x_axis_label='slew distance (deg.)')
for band in band_cmap.transform.factors:
    these_visits = visits.query(f'filter == "{band}"')
    if len(these_visits) > 0:
        p2.circle(x='slewDistance', y='overhead', color=band_cmap, fill_alpha=0.3, source=these_visits, legend_label=band)

legend = p2.legend[0]
legend.orientation = 'horizontal'
p2.add_layout(legend, 'below')

gap_plots = bokeh.layouts.row([p1, p2])

bokeh.io.show(gap_plots)

## Long gaps between exposures

In [20]:
num_gaps = 10
long_gap_visits = visits.sort_values('overhead', ascending=False).query('overhead>30').loc[:, ['start_date', 'overhead', 'slewDistance', 'filter', 'previous_filter']].sort_values('observationId')
long_gap_visits

start_date    overhead  slewDistance  \
observationId                                                                 
574857        2027-11-11 00:26:49.789980928+00:00   65.350099     44.964873   
574858        2027-11-11 00:28:00.498307840+00:00   40.708357     25.259204   
574865        2027-11-11 00:33:19.203398912+00:00   31.224192     18.328972   
574878        2027-11-11 00:42:58.907033856+00:00   44.703145     30.882515   
574928        2027-11-11 01:17:13.089816576+00:00  124.000000      3.165368   
574972        2027-11-11 01:48:14.066727168+00:00  160.000000     62.797226   
575066        2027-11-11 02:51:43.925844992+00:00  160.000000     61.970347   
575110        2027-11-11 03:20:48.978620672+00:00   30.278727     19.682278   
575160        2027-11-11 03:55:35.750685696+00:00  124.000000      2.954887   
575203        2027-11-11 04:26:18.298325760+00:00  160.000000     59.987296   
575224        2027-11-11 04:40:56.239007488+00:00   30.123305     10.764552   
575253        2027-11-11 05:01:59.236823808+00:00  124.000000      2.817896   
575267        2027-11-11 05:12:17.430815488+00:00   49.237083      8.707792   
575328        2027-11-11 05:54:04.170105344+00:00   47.089287     11.492996   
575337        2027-11-11 06:02:11.521555712+00:00  124.000000      2.986112   
575378        2027-11-11 06:29:27.224291072+00:00   47.271224     11.492996   
575435        2027-11-11 07:09:04.405804544+00:00  124.000000      2.810372   
575451        2027-11-11 07:20:06.805913088+00:00   48.545302     10.197480   
575463        2027-11-11 07:28:54.572795136+00:00   31.872447      6.168249   
575475        2027-11-11 07:39:31.172238848+00:00  160.000000     47.041064   
575485        2027-11-11 07:47:29.172221184+00:00  124.000000      0.000000   
575505        2027-11-11 08:01:27.172222208+00:00  124.000000      0.000000   
575515        2027-11-11 08:08:17.048655104+00:00   55.876443     32.169632   
575516        2027-11-11 08:09:23.619486976+00:00   36.570803     28.831878   
575530        2027-11-11 08:21:37.224560384+00:00  157.000000     48.039946   

              filter previous_filter  
observationId                         
574857             i               i  
574858             i               i  
574865             i               i  
574878             i               i  
574928             z               i  
574972             y               z  
575066             z               y  
575110             z               z  
575160             y               z  
575203             r               y  
575224             r               r  
575253             i               r  
575267             i               i  
575328             i               i  
575337             z               i  
575378             z               z  
575435             y               z  
575451             y               y  
575463             y               y  
575475             g               y  
575485             i               g  
575505             r               i  
575515             r               r  
575516             r               r  
575530             z               r

## PSF Width

In [21]:
p = bokeh.plotting.figure(title='PSF Width', y_axis_label='seeingFwhmEff')
for band in band_cmap.transform.factors:
    these_visits = visits.query(f'filter == "{band}"')
    if len(these_visits) > 0:
        p.circle(x='start_date', y='seeingFwhmEff', color=band_cmap, fill_alpha=0.3, source=these_visits, legend_label=band)

p.xaxis[0].formatter = bokeh.models.DatetimeTickFormatter(hours="%H:%M")

legend = p.legend[0]
legend.orientation = 'horizontal'
p.add_layout(legend, 'below')
bokeh.io.show(p)

## Instrumental seeing

In [22]:
# Get a seeing model that applies atmospheric and wavelength corrections, but not instrumental contributions.
seeing_model = rubin_scheduler.site_models.SeeingModel(
    telescope_seeing=0.0,
    optical_design_seeing=0.0,
    camera_seeing=0.0
)
seeing_indx_dict = {}
for i, filtername in enumerate(seeing_model.filter_list):
    seeing_indx_dict[filtername] = i
    
noninstrumental_seeing = np.array(tuple(seeing_model(v.seeingFwhm500, v.airmass)['fwhmEff'][seeing_indx_dict[v['filter']]].item() for i, v in visits.iterrows()))
visits['nonatmo_fwhm'] = np.sqrt(visits['seeingFwhmEff']**2 - noninstrumental_seeing**2)

In [23]:
p = bokeh.plotting.figure(title='Instrumental seeing', y_axis_label='Instrumetal contribution to the FWHM')
for band in band_cmap.transform.factors:
    these_visits = visits.query(f'filter == "{band}"')
    if len(these_visits) > 0:
        p.circle(x='start_date', y='nonatmo_fwhm', color=band_cmap, fill_alpha=0.3, source=these_visits, legend_label=band)

p.xaxis[0].formatter = bokeh.models.DatetimeTickFormatter(hours="%H:%M")

legend = p.legend[0]
legend.orientation = 'horizontal'
p.add_layout(legend, 'below')
bokeh.io.show(p)

This perplexes me; I expected the instrumental contribution in simulations to be constant.

## PSF ellipticity

No ellipticity is simulated by opsim.

## Effective exposure time

In [24]:
p = bokeh.plotting.figure(title='Effective exposure time', y_axis_label=r'Effecive exposure time (sec.)')
for band in band_cmap.transform.factors:
    these_visits = visits.query(f'filter == "{band}"')
    if len(these_visits) > 0:
        p.circle(x='start_date', y='teff', color=band_cmap, fill_alpha=0.3, source=these_visits, legend_label=band)

p.xaxis[0].formatter = bokeh.models.DatetimeTickFormatter(hours="%H:%M")

legend = p.legend[0]
legend.orientation = 'horizontal'
p.add_layout(legend, 'below')
bokeh.io.show(p)

## Sky brightness

When run with current opsim simulations, all simulations are either completely spoiled (infinite extinction) or clear (no extinction), and what is recorded is a fraction of the sky covered by clouds.

So, where the DES nightsum plots the extinction, what is plotted here is the recorded fraction cloud cover.

In [25]:
p = bokeh.plotting.figure(title='Sky brightness', y_axis_label=r'cloud cover')
for band in band_cmap.transform.factors:
    these_visits = visits.query(f'filter == "{band}"')
    if len(these_visits) > 0:
        p.circle(x='start_date', y='cloud', color=band_cmap, fill_alpha=0.3, source=these_visits, legend_label=band)

p.xaxis[0].formatter = bokeh.models.DatetimeTickFormatter(hours="%H:%M")

legend = p.legend[0]
legend.orientation = 'horizontal'
p.add_layout(legend, 'below')
bokeh.io.show(p)

## Visit map

In [26]:
vmap, vmap_data = schedview.plot.visitmap.create_visit_skymaps(
    visits=visits,
    night_date=day_obs_date,
    timezone=timezone,
    observatory=observatory,
)

INFO:healpy:Sigma is 254.796540 arcmin (0.074117 rad) 
INFO:healpy:-> fwhm is 600.000000 arcmin
INFO:healpy:Sigma is 0.000000 arcmin (0.000000 rad) 
INFO:healpy:-> fwhm is 0.000000 arcmin
/sdf/data/rubin/user/neilsen/devel/rubin_scheduler/rubin_scheduler/skybrightness_pre/sky_model_pre.py:277: UserWarning: Requested MJD between sunrise and sunset, returning closest maps
  warnings.warn("Requested MJD between sunrise and sunset, returning closest maps")


In [27]:
bokeh.io.show(vmap)

## Survey Progress

In [28]:
def create_visit_map_for_band(visits, band, conditions, map_hpix, scale_limits=None, palette=colorcet.blues):
    camera_perimeter = LsstCameraFootprintPerimeter()

    plot = bokeh.plotting.figure(
        frame_width=256,
        frame_height=256,
        match_aspect=True,
        title=f"Visits in {band}",
    )
    psphere = Planisphere(mjd=conditions.mjd, plot=plot)

    if scale_limits is None:
        scale_limits = ZScaleInterval().get_limits(map_hpix[~ map_hpix.mask])

    cmap = bokeh.transform.linear_cmap('value', palette, scale_limits[0], scale_limits[1])
    psphere.add_healpix(map_hpix, nside=hp.npix2nside(len(map_hpix)), cmap=cmap)

    band_visits = visits.query(f"filter == '{band}'")

    if len(band_visits)>0:
        ras, decls = camera_perimeter(band_visits.fieldRA, band_visits.fieldDec, band_visits.rotSkyPos)
        
        perimeter_df = pd.DataFrame(
            {
                "ra": ras,
                "decl": decls,
            }
        )
        visit_ds = psphere.add_patches(
            perimeter_df,
            patches_kwargs={
                'fill_color': None,
                'line_color': 'black',
                'line_width': 1
            }
        )

    psphere.decorate()

    psphere.add_marker(
        ra=np.degrees(conditions.sun_ra),
        decl=np.degrees(conditions.sun_dec),
        name="Sun",
        glyph_size=8,
        circle_kwargs={"color": "yellow", "fill_alpha": 1},
    )

    psphere.add_marker(
        ra=np.degrees(conditions.moon_ra),
        decl=np.degrees(conditions.moon_dec),
        name="Moon",
        glyph_size=8,
        circle_kwargs={"color": "orange", "fill_alpha": 0.8},
    )

    return plot

### Map depth accumulated so far

In [29]:
observatory.mjd = night_events.loc['night_middle', 'MJD']
conditions = observatory.return_conditions()

In [30]:
bands = 'ugrizy'
bundle = {}
for band in bands:
    constraint = f"filter == '{band}' AND observationStartMjd < {night_events.loc['sunset', 'MJD']}"
    slicer = maf.HealpixSlicer(nside=32)
    metric = maf.Coaddm5Metric()
    bundle[band] = maf.MetricBundle(metric, slicer, constraint, run_name='last_night')

with baseline_opsim_rp.as_local() as opsim_db_rp:
    bundle_group = maf.MetricBundleGroup(
        bundle, opsim_db_rp.ospath
    )
    bundle_group.run_all()
    depth_hpix = {b: bundle[b].metric_values for b in bands}


Healpix slicer using NSIDE=32, approximate resolution 109.935565 arcminutes
Healpix slicer using NSIDE=32, approximate resolution 109.935565 arcminutes
Healpix slicer using NSIDE=32, approximate resolution 109.935565 arcminutes
Healpix slicer using NSIDE=32, approximate resolution 109.935565 arcminutes
Healpix slicer using NSIDE=32, approximate resolution 109.935565 arcminutes
Healpix slicer using NSIDE=32, approximate resolution 109.935565 arcminutes


In [ ]:
visit_map = {}
for band in 'ugrizy':
    tau_hpix = 10**(0.8*(depth_hpix[band] - fiducial_depth[band]))
    tau_hpix.fill_value = np.nan
    visit_map[band] = create_visit_map_for_band(visits, band, conditions, tau_hpix)

visit_map_grid = bokeh.layouts.gridplot([
    [visit_map['u'], visit_map['g'], visit_map['r']],
    [visit_map['i'], visit_map['z'], visit_map['y']]
])
bokeh.io.show(visit_map_grid)

### Map time since the most recent visits

In [ ]:
bands = 'ugrizy'
bundle = {}
for band in bands:
    constraint = f"filter == '{band}' AND observationStartMjd < {night_events.loc['sunset', 'MJD']}"
    slicer = maf.HealpixSlicer(nside=32)
    metric = maf.MaxMetric('observationStartMJD')
    bundle[band] = maf.MetricBundle(metric, slicer, constraint, run_name='last_night')

with baseline_opsim_rp.as_local() as opsim_db_rp:
    bundle_group = maf.MetricBundleGroup(
        bundle, opsim_db_rp.ospath
    )
    bundle_group.run_all()
    time_since_latest_hpix = {b: night_events.loc['sunset', 'MJD'] - bundle[b].metric_values for b in bands}

In [ ]:
visit_map = {band: create_visit_map_for_band(visits, band, conditions, time_since_latest_hpix[band], [0, 14], 'Viridis256') for band in 'ugrizy'}
visit_map_grid = bokeh.layouts.gridplot([
    [visit_map['u'], visit_map['g'], visit_map['r']],
    [visit_map['i'], visit_map['z'], visit_map['y']]
])
bokeh.io.show(visit_map_grid)

## DDF Cadence

In [ ]:
time_window_duration = 120
ddf_plot_mjds = np.arange(day_obs_mjd - time_window_duration, day_obs_mjd)

In [ ]:
ddf_plot_datetimes = Time(ddf_plot_mjds, format='mjd').datetime
ddf_plot_dates = [datetime.date(t.year, t.month, t.day) for t in ddf_plot_datetimes]
ddf_plot_iso8601 = [str(d) for d in ddf_plot_dates]

In [ ]:
ddf_field_names = tuple(rubin_scheduler.utils.ddf_locations().keys())

In [ ]:
ddf_visits = visit_query(
    baseline_opsim_rp,
    f"""SELECT * FROM observations
    WHERE target IN {tuple(field_name for field_name in ddf_field_names)}
      AND FLOOR(observationStartMJD-0.5)<={day_obs_mjd}
      AND FLOOR(observationStartMJD-0.5)>{day_obs_mjd-time_window_duration}""")

In [ ]:
nightly_ddf = ddf_visits.groupby(['target', 'day_obs_iso8601', 'filter'])['teff'].sum().reset_index()
nightly_ddf = nightly_ddf.pivot(index=['target', 'day_obs_iso8601'], columns='filter', values='teff').fillna(0.0).reset_index().set_index('target')

In [ ]:
cadence_plots = []
bands = band_cmap.transform.factors
ddf_field_names = [fn for fn in ddf_field_names if fn in nightly_ddf.index]
x_range = bokeh.models.FactorRange(factors=ddf_plot_iso8601)

for field_name in ddf_field_names:
    last_plot = len(cadence_plots) == len(ddf_field_names)-1

    df = nightly_ddf.loc[field_name, :]
    figure_kwargs = {
        'x_range' : x_range,
        'title': field_name,
        'frame_height': 150,
        'frame_width': 1024,
        'title_location': 'left',
    }

    if not last_plot:
        figure_kwargs['x_axis_location'] = None

    p = bokeh.plotting.figure(**figure_kwargs)

    p.xaxis.major_label_orientation = 'vertical'

    vbar_stack_kwargs = {
        'stackers': bands,
        'x': 'day_obs_iso8601',
        'width': 0.9,
        'source': df,
        'color': band_cmap.transform.palette,
        'fill_alpha': 0.3,
    }
    if last_plot:
        vbar_stack_kwargs['legend_label'] = bands

    p.vbar_stack(**vbar_stack_kwargs)
    if last_plot:
        legend = p.legend[0]
        legend.orientation = 'horizontal'
        p.add_layout(legend, 'below')
    
    cadence_plots.append(p)

cadence_plot_layout = bokeh.layouts.column(cadence_plots)

bokeh.io.show(cadence_plot_layout)

## Table of exposures

In [ ]:
displayed_columns = ['start_date', 'fieldRA', 'fieldDec', 'filter', 'visitExposureTime', 'numExposures', 'tau', 'skyBrightness', 'seeingFwhmEff', 'cloud', 'note']
displayed_visits_df = visits.loc[:, displayed_columns]
with pd.option_context('display.max_rows', 2000):
    display(displayed_visits_df)

In [ ]:
data_source